# Tutorial to invoke LIME explainers via aix360

There are two ways to use [LIME](https://github.com/marcotcr/lime) explainers after installing aix360:
- [Approach 1  (aix360 style)](#approach1): LIME explainers can be invoked in a manner similar to other explainer algorithms in aix360 via the implemented wrapper classes.
- [Approach 2 (original style)](#approach2): Since LIME comes pre-installed in aix360, the explainers can simply be invoked directly.

This notebook showcases both these approaches to invoke LIME. The notebook is based on the following example from the original LIME tutorial: https://marcotcr.github.io/lime/tutorials/Lime%20-%20multiclass.html

## Approach 1  (aix360 style)
<a id='approach1'></a>
- Note the import statement related to LimeTextExplainer

In [1]:
from __future__ import print_function
import sklearn
import numpy as np
import sklearn
import sklearn.ensemble
import sklearn.metrics

# Importing LimeTextExplainer (aix360 sytle)
from aix360.algorithms.lime import LimeTextExplainer

In [2]:
# Supress jupyter warnings if required for cleaner output
import warnings
warnings.simplefilter('ignore')

### Fetching data, training a classifier

In [3]:
from sklearn.datasets import fetch_20newsgroups
newsgroups_train = fetch_20newsgroups(subset='train')
newsgroups_test = fetch_20newsgroups(subset='test')
# making class names shorter
class_names = [x.split('.')[-1] if 'misc' not in x else '.'.join(x.split('.')[-2:]) for x in newsgroups_train.target_names]
class_names[3] = 'pc.hardware'
class_names[4] = 'mac.hardware'

In [4]:
print(','.join(class_names))

atheism,graphics,ms-windows.misc,pc.hardware,mac.hardware,x,misc.forsale,autos,motorcycles,baseball,hockey,crypt,electronics,med,space,christian,guns,mideast,politics.misc,religion.misc


In [5]:
vectorizer = sklearn.feature_extraction.text.TfidfVectorizer(lowercase=False)
train_vectors = vectorizer.fit_transform(newsgroups_train.data)
test_vectors = vectorizer.transform(newsgroups_test.data)

In [6]:
from sklearn.naive_bayes import MultinomialNB
nb = MultinomialNB(alpha=.01)
nb.fit(train_vectors, newsgroups_train.target)

MultinomialNB(alpha=0.01, class_prior=None, fit_prior=True)

In [7]:
pred = nb.predict(test_vectors)
sklearn.metrics.f1_score(newsgroups_test.target, pred, average='weighted')

0.8350184193998174

### Explaining predictions using lime

In [8]:
from sklearn.pipeline import make_pipeline
c = make_pipeline(vectorizer, nb)

In [9]:
print(c.predict_proba([newsgroups_test.data[0]]).round(3))

[[0.001 0.01  0.003 0.047 0.006 0.002 0.003 0.521 0.022 0.008 0.025 0.
  0.331 0.003 0.006 0.    0.003 0.    0.001 0.009]]


In [10]:
limeexplainer = LimeTextExplainer(class_names=class_names)
print(type(limeexplainer))

<class 'aix360.algorithms.lime.lime_wrapper.LimeTextExplainer'>


In [11]:
idx = 1340
# aix360 style for explaining input instances
exp = limeexplainer.explain_instance(newsgroups_test.data[idx], c.predict_proba, num_features=6, labels=[0, 17])
print('Document id: %d' % idx)
print('Predicted class =', class_names[nb.predict(test_vectors[idx]).reshape(1,-1)[0,0]])
print('True class: %s' % class_names[newsgroups_test.target[idx]])

Document id: 1340
Predicted class = atheism
True class: atheism


In [12]:
print ('Explanation for class %s' % class_names[0])
print ('\n'.join(map(str, exp.as_list(label=0))))
print ()
print ('Explanation for class %s' % class_names[17])
print ('\n'.join(map(str, exp.as_list(label=17))))

Explanation for class atheism
('Caused', 0.2598306611703779)
('Rice', 0.1476407287363688)
('Genocide', 0.13182300286384235)
('scri', -0.09419412002335747)
('certainty', -0.09272741554383297)
('owlnet', -0.08993298975187172)

Explanation for class mideast
('fsu', -0.05535199329931831)
('Theism', -0.05150493402341905)
('Luther', -0.04742295494991691)
('jews', 0.03810985477960863)
('Caused', -0.037706845450166455)
('PBS', 0.031228586744514376)


In [13]:
# aix360 style for explaining input instances
exp = limeexplainer.explain_instance(newsgroups_test.data[idx], c.predict_proba, num_features=6, top_labels=2)
print(exp.available_labels())

[0, 15]


In [14]:
exp.show_in_notebook(text=False)

In [15]:
exp.show_in_notebook(text=newsgroups_test.data[idx], labels=(0,))

## Approach 2 (original style)
<a id='approach2'></a>
- Note the import statement related to LimeTextExplainer

In [16]:
from __future__ import print_function
import sklearn
import numpy as np
import sklearn
import sklearn.ensemble
import sklearn.metrics

# Importing LimeTextExplainer (original style)
from lime.lime_text import LimeTextExplainer

In [17]:
# Supress jupyter warnings if required for cleaner output
import warnings
warnings.simplefilter('ignore')

### Fetching data, training a classifier

In [18]:
from sklearn.datasets import fetch_20newsgroups
newsgroups_train = fetch_20newsgroups(subset='train')
newsgroups_test = fetch_20newsgroups(subset='test')
# making class names shorter
class_names = [x.split('.')[-1] if 'misc' not in x else '.'.join(x.split('.')[-2:]) for x in newsgroups_train.target_names]
class_names[3] = 'pc.hardware'
class_names[4] = 'mac.hardware'

In [19]:
print(','.join(class_names))

atheism,graphics,ms-windows.misc,pc.hardware,mac.hardware,x,misc.forsale,autos,motorcycles,baseball,hockey,crypt,electronics,med,space,christian,guns,mideast,politics.misc,religion.misc


In [20]:
vectorizer = sklearn.feature_extraction.text.TfidfVectorizer(lowercase=False)
train_vectors = vectorizer.fit_transform(newsgroups_train.data)
test_vectors = vectorizer.transform(newsgroups_test.data)

In [21]:
from sklearn.naive_bayes import MultinomialNB
nb = MultinomialNB(alpha=.01)
nb.fit(train_vectors, newsgroups_train.target)

MultinomialNB(alpha=0.01, class_prior=None, fit_prior=True)

In [22]:
pred = nb.predict(test_vectors)
sklearn.metrics.f1_score(newsgroups_test.target, pred, average='weighted')

0.8350184193998174

### Explaining predictions using lime

In [23]:
from sklearn.pipeline import make_pipeline
c = make_pipeline(vectorizer, nb)

In [24]:
print(c.predict_proba([newsgroups_test.data[0]]).round(3))

[[0.001 0.01  0.003 0.047 0.006 0.002 0.003 0.521 0.022 0.008 0.025 0.
  0.331 0.003 0.006 0.    0.003 0.    0.001 0.009]]


In [25]:
explainer = LimeTextExplainer(class_names=class_names)
print(type(explainer))

<class 'lime.lime_text.LimeTextExplainer'>


In [26]:
idx = 1340
# LIME original style for explaining input instances
exp = explainer.explain_instance(newsgroups_test.data[idx], c.predict_proba, num_features=6, labels=[0, 17])
print('Document id: %d' % idx)
print('Predicted class =', class_names[nb.predict(test_vectors[idx]).reshape(1,-1)[0,0]])
print('True class: %s' % class_names[newsgroups_test.target[idx]])

Document id: 1340
Predicted class = atheism
True class: atheism


In [27]:
print ('Explanation for class %s' % class_names[0])
print ('\n'.join(map(str, exp.as_list(label=0))))
print ()
print ('Explanation for class %s' % class_names[17])
print ('\n'.join(map(str, exp.as_list(label=17))))

Explanation for class atheism
('Caused', 0.2601154192014532)
('Rice', 0.14380270774013457)
('Genocide', 0.12202776283712338)
('owlnet', -0.0894833391913411)
('scri', -0.08839334155116563)
('certainty', -0.08588797496264497)

Explanation for class mideast
('fsu', -0.053283740516256506)
('Theism', -0.05103765776729127)
('Luther', -0.04556208403350433)
('jews', 0.03472601688974457)
('Caused', -0.03463184676401465)
('PBS', 0.02914905322207845)


In [28]:
# LIME original style for explaining input instances
exp = explainer.explain_instance(newsgroups_test.data[idx], c.predict_proba, num_features=6, top_labels=2)
print(exp.available_labels())

[0, 15]


In [29]:
exp.show_in_notebook(text=False)

In [30]:
exp.show_in_notebook(text=newsgroups_test.data[idx], labels=(0,))